In [214]:
# coding: utf-8

import requests
import zipfile
import os
import fnmatch

def grep(target_file, input_word):
    grep_list = [line[:-1] for line in [line for line in open(target_file) if line.find(input_word)>=0]]
    return grep_list

def download_file(url):
    dirpath = './data_files/'
    fname =  dirpath + url.split('/')[-1]
    r = requests.get(url, stream=True)
    with open (fname, 'wb') as f:
        for chunk in r.iter_content(chunk_size=1024):
            if chunk:
                f.write(chunk)
                f.flush()
        return fname
    return False

def zip_extract(fname):
    dirpath = './data_files/'
    zfile = zipfile.ZipFile(fname)
    zfile.extractall(dirpath)

if __name__ == '__main__':
    #　保存ファイルの場所
    dirpath = './data_files/'
    
    # 福沢諭吉テキストurlのリストを作る！
    target_file = 'aozora_word_list_utf8.csv'
    input_word = input('find word --> ')
    text_url_list = [line.split(',')[45] for line in grep(target_file, input_word)]
    
    #サーバーからデータをダウンロード && ファイルの展開
    for url in text_url_list:
        fname = download_file(url)
        # fname = './data_files/43029_ruby_23223.zip' #deback
        if fname:
            print('{} is download'.format(fname))
            zip_extract(fname)
        !sleep 1.0

    #すべて展開する
    # txt_list =[./data_files/kyoto_gakkono_ki.txt]
    txt_list = fnmatch.filter(os.listdir(dirpath), '*.txt')
    print(len(fname) == len(txt_list))
    
    #txt_list全体にdirpathを加える
    mapped_txt_list = map(lambda txt_path:dirpath+txt_path, txt_list)

find word --> 福沢,諭吉
./data_files/43029_ruby_23223.zip is download
./data_files/43064_ruby_24472.zip is download
./data_files/45257_ruby_18658.zip is download
./data_files/45664_ruby_24519.zip is download
./data_files/46684_ruby_26314.zip is download
./data_files/46685_ruby_24921.zip is download
./data_files/46686_ruby_24922.zip is download
./data_files/46734_ruby_25781.zip is download
./data_files/46826_ruby_24770.zip is download
./data_files/46827_ruby_24772.zip is download
./data_files/46848_ruby_42407.zip is download
./data_files/46890_ruby_25782.zip is download
./data_files/47030_ruby_26828.zip is download
./data_files/47054_ruby_29646.zip is download
./data_files/47061_ruby_28378.zip is download
./data_files/47063_ruby_32086.zip is download
./data_files/47149_ruby_27921.zip is download
./data_files/47150_ruby_27922.zip is download
./data_files/47151_ruby_27923.zip is download
./data_files/47152_ruby_27924.zip is download
./data_files/47219_ruby_33285.zip is download
./data_files/4

In [47]:
# 正規表現処理を関数化
# mapped_txt_listはgenerateで構成されているため一度使うと消える

import codecs
import re

def processing_regular_expression(text):
    # ヘッダ部分の除去
    text = re.split('-{5,}', text)[2]
    # フッタ部分の除去
    text = re.split('底本：', text)[0]
    # |の除去
    text = text.replace('｜', '')
    text = text.replace('|', '')
    # ルビの除去
    text = re.sub('《.+?》', '', text)
    # 入力注の除去
    text = re.sub('［＃.+?］', '', text)
    # 空行の除去
    text = re.sub('\n\n', '\n', text)
    text = re.sub('\u3000', '', text)
    # CR,LFの除去
    text = re.sub('\r', '', text)
    text = re.sub('\n', '', text)
    return text

if __name__ == '__main__':
    all_sjis_text = "" # 処理済みテキストの格納

    # ファイル読込み、内部表現化
    for text in mapped_txt_list:
        f = codecs.open(text, "r", "sjis")
        sjis_text = f.read()
        f.close()    
        sjis_text = processing_regular_expression(sjis_text)
        all_sjis_text += sjis_text #テキストに保存
        
    # 整形結果確認   
    print(all_sjis_text[:100])
    print('\n\n')
    print(all_sjis_text[-100:])

明治五年申五月朔日、社友早矢仕氏とともに京都にいたり、名所旧跡はもとよりこれを訪うに暇あらず、博覧会の見物ももと余輩上京の趣意にあらず、まず府下の学校を一覧せんとて、知る人に案内を乞い、諸処の学校に行



難きほどのものなれば、貧富ともに勉むべきは学問にして、ただその教場をして仙境ならしめざること、吾々のつねに注意して怠らざるところなれば、学生諸氏もおのおの自から心してこの注意を空しゅうせしむるなかれ。


In [180]:
from janome.tokenizer import Tokenizer

# Tokenneizerインスタンスの生成 
t = Tokenizer()

# テキストを引数として、形態素解析の結果、名詞のみの配列で抽出する関数を定義 
def extract_words(text):
    tokens = t.tokenize(text)
    for token in tokens:
        if token.part_of_speech.split(',')[0] in ['名詞','動詞','形容詞','形容動詞','感動詞']:
            print(token)
    return [token.base_form for token in tokens if  token.part_of_speech.split(',')[0] in ['名詞','動詞','形容詞','形容動詞','感動詞']]
    
if __name__ == '__main__':
    # 全体のテキストを句点で区切った配列にする。
    sentence_list = all_sjis_text.split('。')

    # それぞれの文章を単語リストに変換
    word_list = [extract_words(sentence)for sentence in sentence_list]
    
    # 単語リストの結果を一部表示
    for word in word_list[0]:
        print(word)


明治	名詞,固有名詞,一般,*,*,*,明治,メイジ,メイジ
五	名詞,数,*,*,*,*,五,ゴ,ゴ
年	名詞,接尾,助数詞,*,*,*,年,ネン,ネン
申	名詞,一般,*,*,*,*,申,サル,サル
五月	名詞,副詞可能,*,*,*,*,五月,ゴガツ,ゴガツ
朔日	名詞,一般,*,*,*,*,朔日,サクジツ,サクジツ
社友	名詞,一般,*,*,*,*,社友,シャユウ,シャユー
早	名詞,一般,*,*,*,*,早,ハヤ,ハヤ
矢	名詞,一般,*,*,*,*,矢,ヤ,ヤ
仕	動詞,自立,*,*,五段・ラ行,体言接続特殊２,仕る,ツカマツ,ツカマツ
氏	名詞,接尾,人名,*,*,*,氏,シ,シ
京都	名詞,固有名詞,地域,一般,*,*,京都,キョウト,キョート
い	動詞,自立,*,*,一段,連用形,いる,イ,イ
名所旧跡	名詞,一般,*,*,*,*,名所旧跡,メイショキュウセキ,メイショキューセキ
これ	名詞,代名詞,一般,*,*,*,これ,コレ,コレ
訪う	動詞,自立,*,*,五段・ワ行促音便,基本形,訪う,オトナウ,オトナウ
暇	名詞,一般,*,*,*,*,暇,ヒマ,ヒマ
あら	動詞,自立,*,*,五段・ラ行,未然形,ある,アラ,アラ
博覧	名詞,サ変接続,*,*,*,*,博覧,ハクラン,ハクラン
会	名詞,接尾,一般,*,*,*,会,カイ,カイ
見物	名詞,サ変接続,*,*,*,*,見物,ケンブツ,ケンブツ
もと	名詞,一般,*,*,*,*,もと,モト,モト
余	名詞,接尾,一般,*,*,*,余,ヨ,ヨ
輩	名詞,一般,*,*,*,*,輩,トモガラ,トモガラ
上京	名詞,サ変接続,*,*,*,*,上京,ジョウキョウ,ジョーキョー
趣意	名詞,一般,*,*,*,*,趣意,シュイ,シュイ
あら	動詞,自立,*,*,五段・ラ行,未然形,ある,アラ,アラ
府下	名詞,一般,*,*,*,*,府下,フカ,フカ
学校	名詞,一般,*,*,*,*,学校,ガッコウ,ガッコー
一覧	名詞,サ変接続,*,*,*,*,一覧,イチラン,イチラン
せ	動詞,自立,*,*,サ変・スル,未然ヌ接続,する,セ,セ
知る	動詞,自立,*,*,五段・ラ行,基本形,知る,シル,シル
人	名詞,一般,*,*,*,*,人,ヒト,ヒト
案内	名詞,サ変接続,*,*,*,*,案内,アンナイ,アンナイ
乞い	名

講ずる	動詞,自立,*,*,サ変・−ズル,基本形,講ずる,コウズル,コーズル
ところ	名詞,非自立,副詞可能,*,*,*,ところ,トコロ,トコロ
書	名詞,一般,*,*,*,*,書,ショ,ショ
翻訳	名詞,サ変接続,*,*,*,*,翻訳,ホンヤク,ホンヤク
書	名詞,接尾,一般,*,*,*,書,ショ,ショ
用い	動詞,自立,*,*,一段,連用形,用いる,モチイ,モチイ
足ら	動詞,自立,*,*,五段・ラ行,未然形,足る,タラ,タラ
とき	名詞,非自立,副詞可能,*,*,*,とき,トキ,トキ
漢書	名詞,一般,*,*,*,*,漢書,カンショ,カンショ
講じ	動詞,自立,*,*,一段,連用形,講じる,コウジ,コージ
字義	名詞,一般,*,*,*,*,字義,ジギ,ジギ
説く	動詞,自立,*,*,五段・カ行イ音便,基本形,説く,トク,トク
あら	動詞,自立,*,*,五段・ラ行,未然形,ある,アラ,アラ
断章	名詞,一般,*,*,*,*,断章,ダンショウ,ダンショー
取	動詞,自立,*,*,五段・ラ行,体言接続特殊２,取る,ト,ト
義	名詞,固有名詞,人名,名,*,*,義,ヨシ,ヨシ
もっ	動詞,自立,*,*,五段・タ行,連用タ接続,もつ,モッ,モッ
文明	名詞,一般,*,*,*,*,文明,ブンメイ,ブンメイ
趣旨	名詞,一般,*,*,*,*,趣旨,シュシ,シュシ
述	名詞,一般,*,*,*,*,述,ジュツ,ジュツ
ぶる	動詞,自立,*,*,五段・ラ行,基本形,ぶる,ブル,ブル
主	名詞,形容動詞語幹,*,*,*,*,主,オモ,オモ
せり	名詞,一般,*,*,*,*,せり,セリ,セリ
小学校	名詞,一般,*,*,*,*,小学校,ショウガッコウ,ショーガッコー
費用	名詞,一般,*,*,*,*,費用,ヒヨウ,ヒヨー
はじめ	名詞,副詞可能,*,*,*,*,はじめ,ハジメ,ハジメ
これ	名詞,代名詞,一般,*,*,*,これ,コレ,コレ
建つ	動詞,自立,*,*,五段・タ行,基本形,建つ,タツ,タツ
とき	名詞,非自立,副詞可能,*,*,*,とき,トキ,トキ
半	名詞,一般,*,*,*,*,半,ハン,ハン
官	名詞,一般,*,*,*,*,官,カン,カン
たすけ	動詞,自立,*,*,一段,連用形,たすける,タスケ,タスケ
半	名詞,一般,*,*,*,*,半,ハン,ハン
市中	名詞,一

等級	名詞,一般,*,*,*,*,等級,トウキュウ,トーキュー
より	動詞,自立,*,*,五段・ラ行,連用形,よる,ヨリ,ヨリ
月給	名詞,一般,*,*,*,*,月給,ゲッキュウ,ゲッキュー
から	動詞,自立,*,*,五段・ラ行,未然形,かる,カラ,カラ
多き	形容詞,自立,*,*,形容詞・アウオ段,体言接続,多い,オオキ,オーキ
七	名詞,数,*,*,*,*,七,ナナ,ナナ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
両	名詞,接尾,助数詞,*,*,*,両,リョウ,リョー
少なき	形容詞,自立,*,*,形容詞・アウオ段,体言接続,少ない,スクナキ,スクナキ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
五	名詞,数,*,*,*,*,五,ゴ,ゴ
両	名詞,接尾,助数詞,*,*,*,両,リョウ,リョー
二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
両	名詞,接尾,助数詞,*,*,*,両,リョウ,リョー
平均	名詞,サ変接続,*,*,*,*,平均,ヘイキン,ヘイキン
一	名詞,数,*,*,*,*,一,イチ,イチ
人	名詞,接尾,助数詞,*,*,*,人,ニン,ニン
二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
五	名詞,数,*,*,*,*,五,ゴ,ゴ
両	名詞,接尾,助数詞,*,*,*,両,リョウ,リョー
過ぎ	動詞,自立,*,*,一段,未然形,過ぎる,スギ,スギ
二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
人	名詞,接尾,助数詞,*,*,*,人,ニン,ニン
一月	名詞,副詞可能,*,*,*,*,一月,イチガツ,イチガツ
五	名詞,数,*,*,*,*,五,ゴ,ゴ
百	名詞,数,*,*,*,*,百,ヒャク,ヒャク
両	名詞,接尾,助数詞,*,*,*,両,リョウ,リョー
官	名詞,一般,*,*,*,*,官,カン,カン
費用	名詞,一般,*,*,*,*,費用,ヒヨウ,ヒヨー
少く	形容詞,自立,*,*,形容詞・アウオ段,連用テ接続,少い,スクナク,スクナク
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
事務	名詞,一般,*,*,*,*,事務,ジム,ジム
整う	動詞,自立,*,*,五段・ワ行促音便,基本形,整う,トトノウ

され	動詞,自立,*,*,五段・ラ行,仮定形,さる,サレ,サレ
経済	名詞,一般,*,*,*,*,経済,ケイザイ,ケイザイ
商売	名詞,サ変接続,*,*,*,*,商売,ショウバイ,ショーバイ
道理	名詞,一般,*,*,*,*,道理,ドウリ,ドーリ
英	名詞,固有名詞,地域,国,*,*,英,エイ,エイ
亜	名詞,固有名詞,地域,一般,*,*,亜,ア,ア
両国	名詞,一般,*,*,*,*,両国,リョウコク,リョーコク
趣	名詞,一般,*,*,*,*,趣,オモムキ,オモムキ
する	動詞,自立,*,*,サ変・スル,基本形,する,スル,スル
もの	名詞,非自立,一般,*,*,*,もの,モノ,モノ
いわ	動詞,自立,*,*,五段・ワ行促音便,未然形,いう,イワ,イワ
え	動詞,自立,*,*,一段,未然形,える,エ,エ
物理	名詞,一般,*,*,*,*,物理,ブツリ,ブツリ
ら	名詞,接尾,一般,*,*,*,ら,ラ,ラ
開闢	名詞,一般,*,*,*,*,開闢,カイビャク,カイビャク
初	名詞,一般,*,*,*,*,初,ハツ,ハツ
今日	名詞,副詞可能,*,*,*,*,今日,キョウ,キョー
いたる	動詞,自立,*,*,五段・ラ行,基本形,いたる,イタル,イタル
世界	名詞,一般,*,*,*,*,世界,セカイ,セカイ
古今	名詞,一般,*,*,*,*,古今,ココン,ココン
一	名詞,数,*,*,*,*,一,イチ,イチ
様	名詞,接尾,人名,*,*,*,様,サマ,サマ
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
変	名詞,形容動詞語幹,*,*,*,*,変,ヘン,ヘン
違	名詞,一般,*,*,*,*,違,*,*
ある	動詞,自立,*,*,五段・ラ行,基本形,ある,アル,アル
こと	名詞,非自立,一般,*,*,*,こと,コト,コト
なし	形容詞,自立,*,*,形容詞・アウオ段,文語基本形,ない,ナシ,ナシ
神代	名詞,一般,*,*,*,*,神代,カミヨ,カミヨ
水	名詞,一般,*,*,*,*,水,ミズ,ミズ
華氏	名詞,一般,*,*,*,*,華氏,カシ,カシ
寒暖計	名詞,一般,*,*,*,*,寒暖計,カンダンケイ,カンダンケイ
二	名詞,数,*,*,*,*,二,ニ,ニ
百	名詞,数,*,*,*,*,百,ヒャク,ヒャク
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
二	名

無稽	名詞,一般,*,*,*,*,無稽,ムケイ,ムケイ
幽冥	名詞,一般,*,*,*,*,幽冥,ユウメイ,ユーメイ
説	名詞,接尾,一般,*,*,*,説,セツ,セツ
惑溺	名詞,サ変接続,*,*,*,*,惑溺,ワクデキ,ワクデキ
する	動詞,自立,*,*,サ変・スル,基本形,する,スル,スル
こと	名詞,非自立,一般,*,*,*,こと,コト,コト
少なし	形容詞,自立,*,*,形容詞・アウオ段,文語基本形,少ない,スクナシ,スクナシ
いえ	動詞,自立,*,*,五段・ワ行促音便,仮定形,いう,イエ,イエ
これ	名詞,代名詞,一般,*,*,*,これ,コレ,コレ
惑溺	名詞,サ変接続,*,*,*,*,惑溺,ワクデキ,ワクデキ
せ	動詞,自立,*,*,サ変・スル,未然ヌ接続,する,セ,セ
一時	名詞,副詞可能,*,*,*,*,一時,イチジ,イチジ
仏者	名詞,一般,*,*,*,*,仏者,ブッシャ,ブッシャ
敵する	動詞,自立,*,*,サ変・−スル,基本形,敵する,テキスル,テキスル
の	名詞,非自立,一般,*,*,*,の,ノ,ノ
熱心	名詞,形容動詞語幹,*,*,*,*,熱心,ネッシン,ネッシン
乗じ	動詞,自立,*,*,一段,連用形,乗じる,ジョウジ,ジョージ
もの	名詞,非自立,一般,*,*,*,もの,モノ,モノ
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
天然	名詞,一般,*,*,*,*,天然,テンネン,テンネン
真理	名詞,一般,*,*,*,*,真理,シンリ,シンリ
原則	名詞,一般,*,*,*,*,原則,ゲンソク,ゲンソク
推究	名詞,一般,*,*,*,*,推究,*,*
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
知識	名詞,一般,*,*,*,*,知識,チシキ,チシキ
働	名詞,一般,*,*,*,*,働,*,*
ざる	名詞,一般,*,*,*,*,ざる,ザル,ザル
幽冥	名詞,一般,*,*,*,*,幽冥,ユウメイ,ユーメイ
説	名詞,接尾,一般,*,*,*,説,セツ,セツ
向っ	動詞,自立,*,*,五段・ワ行促音便,連用タ接続,向う,ムカッ,ムカッ
淡白	名詞,形容動詞語幹,*,*,*,*,淡白,タンパク,タンパク
物理	名詞,一般,*,*,*,*,物理,ブツリ,ブツリ
の	名詞,非自立,一般,*,*,*,の,ノ,ノ
情	名詞,一般,*,

...

二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
年	名詞,接尾,助数詞,*,*,*,年,ネン,ネン
前	名詞,副詞可能,*,*,*,*,前,マエ,マエ
君	名詞,代名詞,一般,*,*,*,君,キミ,キミ
齢	名詞,一般,*,*,*,*,齢,ヨワイ,ヨワイ
ひとし	名詞,固有名詞,人名,名,*,*,ひとし,ヒトシ,ヒトシ
我々	名詞,代名詞,一般,*,*,*,我々,ワレワレ,ワレワレ
挙動	名詞,一般,*,*,*,*,挙動,キョドウ,キョドー
軽躁	名詞,形容動詞語幹,*,*,*,*,軽躁,ケイソウ,ケイソー
二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
年	名詞,接尾,助数詞,*,*,*,年,ネン,ネン
前	名詞,副詞可能,*,*,*,*,前,マエ,マエ
君	名詞,代名詞,一般,*,*,*,君,キミ,キミ
比すれ	動詞,自立,*,*,サ変・−スル,仮定形,比する,ヒスレ,ヒスレ
深く	形容詞,自立,*,*,形容詞・アウオ段,連用テ接続,深い,フカク,フカク
譴責	名詞,サ変接続,*,*,*,*,譴責,ケンセキ,ケンセキ
蒙る	動詞,自立,*,*,五段・ラ行,基本形,蒙る,コウムル,コームル
理	名詞,一般,*,*,*,*,理,リ,リ
なし	形容詞,自立,*,*,形容詞・アウオ段,文語基本形,ない,ナシ,ナシ
君	名詞,代名詞,一般,*,*,*,君,キミ,キミ
幕府	名詞,一般,*,*,*,*,幕府,バクフ,バクフ
末世	名詞,一般,*,*,*,*,末世,マッセ,マッセ
あたり	動詞,自立,*,*,五段・ラ行,連用形,あたる,アタリ,アタリ
乱	名詞,一般,*,*,*,*,乱,ラン,ラン
処し	動詞,自立,*,*,五段・サ行,連用形,処す,ショシ,ショシ
維新	名詞,一般,*,*,*,*,維新,イシン,イシン
初	名詞,一般,*,*,*,*,初,ハツ,ハツ
創業	名詞,サ変接続,*,*,*,*,創業,ソウギョウ,ソーギョー
際し	動詞,自立,*,*,五段・サ行,連用形,際す,サイシ,サイシ
こと	名詞,非自立,一般,*,*,*,こと,コト,コト
なれ	動詞,自立,*,*,五段・ラ行,仮定形,なる,ナレ,ナレ
今日	名詞,副詞可能,*,*,*,*,今日,キョウ,キョー
我々	名詞,

保ち	動詞,自立,*,*,五段・タ行,連用形,保つ,タモチ,タモチ
もっ	動詞,自立,*,*,五段・タ行,連用タ接続,もつ,モッ,モッ
朋友	名詞,一般,*,*,*,*,朋友,ホウユウ,ホーユー
信	名詞,一般,*,*,*,*,信,シン,シン
固う	形容詞,自立,*,*,形容詞・アウオ段,連用ゴザイ接続,固い,カタウ,カター
人生	名詞,一般,*,*,*,*,人生,ジンセイ,ジンセイ
居	名詞,一般,*,*,*,*,居,キョ,キョ
家	名詞,接尾,一般,*,*,*,家,カ,カ
細目	名詞,一般,*,*,*,*,細目,ホソメ,ホソメ
天下	名詞,一般,*,*,*,*,天下,テンカ,テンカ
大計	名詞,一般,*,*,*,*,大計,タイケイ,タイケイ
いたる	動詞,自立,*,*,五段・ラ行,基本形,いたる,イタル,イタル
一切	名詞,副詞可能,*,*,*,*,一切,イッサイ,イッサイ
秩序	名詞,一般,*,*,*,*,秩序,チツジョ,チツジョ
包	名詞,一般,*,*,*,*,包,ツツミ,ツツミ
羅	名詞,固有名詞,人名,姓,*,*,羅,ラ,ラ
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
洩らす	動詞,自立,*,*,五段・サ行,基本形,洩らす,モラス,モラス
もの	名詞,非自立,一般,*,*,*,もの,モノ,モノ
ある	動詞,自立,*,*,五段・ラ行,基本形,ある,アル,アル
輩	名詞,一般,*,*,*,*,輩,トモガラ,トモガラ
世	名詞,一般,*,*,*,*,世,ヨ,ヨ
教育	名詞,サ変接続,*,*,*,*,教育,キョウイク,キョーイク
論	名詞,接尾,一般,*,*,*,論,ロン,ロン
者	名詞,接尾,一般,*,*,*,者,シャ,シャ
古来	名詞,一般,*,*,*,*,古来,コライ,コライ
典	名詞,一般,*,*,*,*,典,テン,テン
経	名詞,一般,*,*,*,*,経,ケイ,ケイ
徳育	名詞,一般,*,*,*,*,徳育,トクイク,トクイク
用	名詞,一般,*,*,*,*,用,ヨウ,ヨー
供せ	動詞,自立,*,*,サ変・−スル,未然レル接続,供する,キョウセ,キョーセ
ん	名詞,非自立,一般,*,*,*,ん,ン,ン
する	動詞,自立,*,*,サ変・スル,基本形,する,スル,スル
咎	名詞,一般,*,*,*,*,咎,トガ,トガ
ざれ	動詞,自立,*,*,一

任務	名詞,一般,*,*,*,*,任務,ニンム,ニンム
為す	動詞,自立,*,*,五段・サ行,基本形,為す,ナス,ナス
是	名詞,一般,*,*,*,*,是,ゼ,ゼ
国民	名詞,一般,*,*,*,*,国民,コクミン,コクミン
軍事	名詞,一般,*,*,*,*,軍事,グンジ,グンジ
服し	動詞,自立,*,*,五段・サ行,連用形,服す,フクシ,フクシ
国費	名詞,一般,*,*,*,*,国費,コクヒ,コクヒ
負担	名詞,サ変接続,*,*,*,*,負担,フタン,フタン
する	動詞,自立,*,*,サ変・スル,基本形,する,スル,スル
義務	名詞,一般,*,*,*,*,義務,ギム,ギム
あり	動詞,自立,*,*,五段・ラ行,連用形,ある,アリ,アリ
二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
三	名詞,数,*,*,*,*,三,サン,サン
条	名詞,接尾,助数詞,*,*,*,条,ジョウ,ジョー
軍事	名詞,一般,*,*,*,*,軍事,グンジ,グンジ
服し	動詞,自立,*,*,五段・サ行,連用形,服す,フクシ,フクシ
国費	名詞,一般,*,*,*,*,国費,コクヒ,コクヒ
負担	名詞,サ変接続,*,*,*,*,負担,フタン,フタン
すれ	動詞,自立,*,*,サ変・スル,仮定形,する,スレ,スレ
国	名詞,一般,*,*,*,*,国,クニ,クニ
立法	名詞,一般,*,*,*,*,立法,リッポウ,リッポー
参与	名詞,サ変接続,*,*,*,*,参与,サンヨ,サンヨ
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
国費	名詞,一般,*,*,*,*,国費,コクヒ,コクヒ
用途	名詞,一般,*,*,*,*,用途,ヨウト,ヨート
監督	名詞,サ変接続,*,*,*,*,監督,カントク,カントク
する	動詞,自立,*,*,サ変・スル,基本形,する,スル,スル
国民	名詞,一般,*,*,*,*,国民,コクミン,コクミン
権利	名詞,一般,*,*,*,*,権利,ケンリ,ケンリ
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
其義務	名詞,一般,*,*,*,*,其義務,*,*
二	名詞,数,*,*,*,*,二,ニ,ニ
十	名詞,数,*,*,*,*,十,ジュウ,ジュー
四	名詞,数,*,*,*,*,四,ヨン,ヨン
条	名詞,接尾,助数詞,*,

教育	名詞,サ変接続,*,*,*,*,教育,キョウイク,キョーイク
かく	名詞,一般,*,*,*,*,かく,カク,カク
齟齬	名詞,サ変接続,*,*,*,*,齟齬,ソゴ,ソゴ
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
尋	名詞,一般,*,*,*,*,尋,ヒロ,ヒロ
ぬる	動詞,自立,*,*,五段・ラ行,基本形,ぬる,ヌル,ヌル
教育	名詞,サ変接続,*,*,*,*,教育,キョウイク,キョーイク
行き	動詞,自立,*,*,五段・カ行促音便,連用形,行く,イキ,イキ
とどけ	動詞,自立,*,*,五段・カ行イ音便,仮定形,とどく,トドケ,トドケ
文明	名詞,一般,*,*,*,*,文明,ブンメイ,ブンメイ
進歩	名詞,サ変接続,*,*,*,*,進歩,シンポ,シンポ
一切	名詞,副詞可能,*,*,*,*,一切,イッサイ,イッサイ
万事	名詞,一般,*,*,*,*,万事,バンジ,バンジ
意	名詞,一般,*,*,*,*,意,イ,イ
なら	動詞,自立,*,*,五段・ラ行,未然形,なる,ナラ,ナラ
はなし	名詞,一般,*,*,*,*,はなし,ハナシ,ハナシ
信じ	動詞,自立,*,*,一段,連用形,信じる,シンジ,シンジ
教育	名詞,サ変接続,*,*,*,*,教育,キョウイク,キョーイク
人間	名詞,一般,*,*,*,*,人間,ニンゲン,ニンゲン
世界	名詞,一般,*,*,*,*,世界,セカイ,セカイ
用	名詞,一般,*,*,*,*,用,ヨウ,ヨー
うる	動詞,自立,*,*,一段・得ル,基本形,うる,ウル,ウル
工	名詞,一般,*,*,*,*,工,コウ,コー
風	名詞,接尾,一般,*,*,*,風,フウ,フー
忘れ	動詞,自立,*,*,一段,連用形,忘れる,ワスレ,ワスレ
罪	名詞,一般,*,*,*,*,罪,ツミ,ツミ
答え	動詞,自立,*,*,一段,未然形,答える,コタエ,コタエ
え	動詞,自立,*,*,一段,未然形,える,エ,エ
人間	名詞,一般,*,*,*,*,人間,ニンゲン,ニンゲン
世界	名詞,一般,*,*,*,*,世界,セカイ,セカイ
存外	名詞,形容動詞語幹,*,*,*,*,存外,ゾンガイ,ゾンガイ
広く	形容詞,自立,*,*,形容詞・アウオ段,連用テ接続,広い,ヒロク,ヒロク
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
存外	名詞,形容動詞語

生徒	名詞,一般,*,*,*,*,生徒,セイト,セイト
中	名詞,接尾,副詞可能,*,*,*,中,チュウ,チュー
行状	名詞,一般,*,*,*,*,行状,ギョウジョウ,ギョージョー
者	名詞,非自立,一般,*,*,*,者,モノ,モノ
なき	形容詞,自立,*,*,形容詞・アウオ段,体言接続,ない,ナキ,ナキ
いえ	動詞,自立,*,*,五段・ワ行促音便,仮定形,いう,イエ,イエ
他	名詞,一般,*,*,*,*,他,タ,タ
公私	名詞,一般,*,*,*,*,公私,コウシ,コーシ
学校	名詞,一般,*,*,*,*,学校,ガッコウ,ガッコー
生徒	名詞,一般,*,*,*,*,生徒,セイト,セイト
比し	動詞,自立,*,*,五段・サ行,連用形,比す,ヒシ,ヒシ
慶応義塾	名詞,固有名詞,組織,*,*,*,慶応義塾,ケイオウギジュク,ケイオーギジュク
生徒	名詞,一般,*,*,*,*,生徒,セイト,セイト
徳義	名詞,一般,*,*,*,*,徳義,トクギ,トクギ
薄き	形容詞,自立,*,*,形容詞・アウオ段,体言接続,薄い,ウスキ,ウスキ
者	名詞,接尾,一般,*,*,*,者,シャ,シャ
否	名詞,一般,*,*,*,*,否,イナ,イナ
品行	名詞,一般,*,*,*,*,品行,ヒンコウ,ヒンコー
方正	名詞,一般,*,*,*,*,方正,ホウセイ,ホーセイ
謹直	名詞,一般,*,*,*,*,謹直,キンチョク,キンチョク
し	動詞,自立,*,*,サ変・スル,連用形,する,シ,シ
世事	名詞,一般,*,*,*,*,世事,セジ,セジ
政談	名詞,サ変接続,*,*,*,*,政談,セイダン,セイダン
着実	名詞,形容動詞語幹,*,*,*,*,着実,チャクジツ,チャクジツ
名	名詞,一般,*,*,*,*,名,ナ,ナ
博し	動詞,自立,*,*,五段・サ行,連用形,博す,ハクシ,ハクシ
塾	名詞,一般,*,*,*,*,塾,ジュク,ジュク
中	名詞,接尾,副詞可能,*,*,*,中,チュウ,チュー
静謐	名詞,形容動詞語幹,*,*,*,*,静謐,セイヒツ,セイヒツ
他	名詞,一般,*,*,*,*,他,タ,タ
比類	名詞,サ変接続,*,*,*,*,比類,ヒルイ,ヒルイ
見る	動詞,自立,*,*,一段,基本形,見る,ミル,ミル
こと	名詞,非自立,一般,*,*,*,こと,コト,コト
稀	名詞,形容動詞語幹,*

In [156]:
#word2vecの使い方を調べる
#適切なハイパーパラメータを決める

import gensim
model = gensim.models.Word2Vec(
    word_list, 
    sg = 1,
    size = 100, # 次元
    window = 15, #similar_words 
    min_count = 1,
    hs = 0,
    workers = 2,
    sorted_vocab=True
)
model.train(word_list, total_examples=len(word_list), epochs=5)

(427409, 495975)

In [207]:
#福沢諭吉に関連するワードを任意で入力して見つけよう！

# 結果の確認
w1='諭吉'
w2= input('free word -->')
try:
    #２つの単語の類似性を数値で出す。
    print(model.wv.similarity(w1, w2))
    
    print('\n') # 改行
    
    #他の類似性の高い単語の表示
    print('類似性が高いワード')
    pos_w = model.wv.most_similar(positive=w2, topn=5)
    for item in pos_w:
        print(item[0], item[1])
    
    print('\n')
    
    print('類似性が低いワード')
    neg_w = model.wv.most_similar(negative=w2, topn=5)
    for item in neg_w:
        print(item[0], item[1])
        
except:
    print('{}は類似性がありません'.format(w2))

free word -->世間
0.23184745


類似性が高いワード
得意 0.8046280145645142
無頼 0.8010901808738708
しかる 0.7597963809967041
珍 0.7592639923095703
最中 0.7563234567642212


類似性が低いワード
絵入り -0.009524280205368996
シ -0.11636762320995331
ヲ -0.11850329488515854
シテ -0.11987338215112686
テ -0.12625446915626526


/Users/hamaguchikazuki/.pyenv/versions/3.6.5/envs/ppgVC/lib/python3.6/site-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):
